In [1]:
import altair as alt
import pandas as pd
from scipy import stats  # (widely used, standard)
# Using this syntax allows use to write `stats` instead of `scipy.stats`.
from sklearn.linear_model import LinearRegression
import pingouin as pg  # (optional, recommended)
import numpy as np
import matplotlib.pyplot as plt
#import statsmodels.api as sm
from statsmodels.stats.multicomp import pairwise_tukeyhsd

**We will set an alpha of 0.05 for all the following hypothesis tests.**

# Overdose related calls to the police

In [2]:
overdose_calls = pd.read_csv('../clean_datasets/Overdose_calls.csv')

In [3]:
overdose_calls_postCovid = overdose_calls[overdose_calls['YEAR']>=2020]
overdose_calls_postCovid

REP_DATE        DOW  YEAR NARCAN_ADM  HOUR  DAY  MONTH
1030  2020-08-31 04:00:00+00:00     Monday  2020    Unknown     4   31      8
1031  2020-09-10 04:00:00+00:00   Thursday  2020    Unknown     4   10      9
1032  2020-09-04 04:00:00+00:00     Friday  2020    Unknown     4    4      9
1033  2020-07-20 04:00:00+00:00     Monday  2020    Unknown     4   20      7
1034  2020-08-18 04:00:00+00:00    Tuesday  2020    Unknown     4   18      8
...                         ...        ...   ...        ...   ...  ...    ...
2874  2022-09-13 04:00:00+00:00    Tuesday  2022    Unknown     4   13      9
2875  2022-05-08 04:00:00+00:00  Wednesday  2022    Unknown     4    8      5
2876  2022-08-28 04:00:00+00:00   Thursday  2022    Unknown     4   28      8
2877  2022-02-17 05:00:00+00:00     Friday  2022        Yes     5   17      2
2878  2022-11-12 05:00:00+00:00  Wednesday  2022        Yes     5   12     11

[1849 rows x 7 columns]

In [4]:
overdose_calls_preCovid = overdose_calls[overdose_calls['YEAR']<2020]
overdose_calls_preCovid

REP_DATE        DOW  YEAR NARCAN_ADM  HOUR  DAY  MONTH
0     2017-08-31 04:00:00+00:00   Thursday  2017    Unknown     4   31      8
1     2017-08-11 04:00:00+00:00     Friday  2017    Unknown     4   11      8
2     2017-07-31 04:00:00+00:00     Monday  2017    Unknown     4   31      7
3     2017-06-27 04:00:00+00:00    Tuesday  2017    Unknown     4   27      6
4     2017-04-29 04:00:00+00:00   Saturday  2017    Unknown     4   29      4
...                         ...        ...   ...        ...   ...  ...    ...
1025  2019-05-19 04:00:00+00:00     Sunday  2019    Unknown     4   19      5
1026  2019-09-26 04:00:00+00:00   Thursday  2019    Unknown     4   26      9
1027  2019-05-30 04:00:00+00:00   Thursday  2019    Unknown     4   30      5
1028  2019-06-09 04:00:00+00:00     Sunday  2019    Unknown     4    9      6
1029  2019-06-26 04:00:00+00:00  Wednesday  2019    Unknown     4   26      6

[1030 rows x 7 columns]

In [5]:
overdose_calls.head()

REP_DATE       DOW  YEAR NARCAN_ADM  HOUR  DAY  MONTH
0  2017-08-31 04:00:00+00:00  Thursday  2017    Unknown     4   31      8
1  2017-08-11 04:00:00+00:00    Friday  2017    Unknown     4   11      8
2  2017-07-31 04:00:00+00:00    Monday  2017    Unknown     4   31      7
3  2017-06-27 04:00:00+00:00   Tuesday  2017    Unknown     4   27      6
4  2017-04-29 04:00:00+00:00  Saturday  2017    Unknown     4   29      4

In [6]:
days_order = ['Monday', 'Tuesday', 'Wednesday', 'Thursday', 'Friday', 'Saturday', 'Sunday']

In [7]:
# Group by 'YEAR' and 'DOW', and count the occurrences (which represent calls)
grouped_YEAR_DOW = overdose_calls.groupby(['YEAR', 'DOW']).size().reset_index(name='CALLS')
# Pivot the table to get 'DOW' as columns and 'YEAR' as index
pivot_YEAR_DOW = grouped_YEAR_DOW.pivot_table(index='YEAR', columns='DOW', values='CALLS', fill_value=0)
# SORT BY day
pivot_YEAR_DOW = pivot_YEAR_DOW[days_order]
# Reset index to make 'YEAR' a regular column
pivot_YEAR_DOW.reset_index(inplace=True)
# Display the resulting DataFrame
pivot_YEAR_DOW

DOW  YEAR  Monday  Tuesday  Wednesday  Thursday  Friday  Saturday  Sunday
0    2017      30       33         35        49      33        51      50
1    2018      43       43         35        40      50        70      44
2    2019      45       64         56        57      75        56      71
3    2020      67       78         86        67      99        67      74
4    2021      87      100         98        92      98        94      77
5    2022      91      100        101        98      98        98      79

In [8]:
grouped_YEAR_DAY = overdose_calls.groupby(['YEAR', 'DAY']).size().reset_index(name='CALLS')
pivot_YEAR_DAY = grouped_YEAR_DAY.pivot_table(index='YEAR', columns='DAY', values='CALLS', fill_value=0)
pivot_YEAR_DAY.reset_index(inplace=True)
pivot_YEAR_DAY

DAY  YEAR   1   2   3   4   5   6   7   8   9  ...  22  23  24  25  26  27  \
0    2017  14  12  11   6  13   9  13   6  10  ...   8  14   5  10   5  13   
1    2018  25  13  19  18   8   9   7   5  14  ...  13  10   9   9  12   9   
2    2019  33  21  22  11  12  14  17   8   9  ...  12   9  15  15  11  11   
3    2020  26  24  21  22  14  18  20  13  21  ...  18  18  14  15  14  11   
4    2021  30  34  29  22  21  22  21  17  23  ...  15  15  28  20  23  19   
5    2022  33  23  27  27  31  27  14  21  26  ...  14  23  27  19  22  18   

DAY  28  29  30  31  
0     6   8  11   7  
1    10   8  12  10  
2    14  14  18  14  
3    14  16  14  19  
4    20  16  27  13  
5    25  11  22  13  

[6 rows x 32 columns]

In [9]:
pivot_YEAR_DAY_preCovid=pivot_YEAR_DAY[pivot_YEAR_DAY['YEAR']<2020]
pivot_YEAR_DAY_preCovid

DAY  YEAR   1   2   3   4   5   6   7  8   9  ...  22  23  24  25  26  27  28  \
0    2017  14  12  11   6  13   9  13  6  10  ...   8  14   5  10   5  13   6   
1    2018  25  13  19  18   8   9   7  5  14  ...  13  10   9   9  12   9  10   
2    2019  33  21  22  11  12  14  17  8   9  ...  12   9  15  15  11  11  14   

DAY  29  30  31  
0     8  11   7  
1     8  12  10  
2    14  18  14  

[3 rows x 32 columns]

In [10]:
pivot_YEAR_DAY_postCovid=pivot_YEAR_DAY[pivot_YEAR_DAY['YEAR']>=2020]
pivot_YEAR_DAY_postCovid

DAY  YEAR   1   2   3   4   5   6   7   8   9  ...  22  23  24  25  26  27  \
3    2020  26  24  21  22  14  18  20  13  21  ...  18  18  14  15  14  11   
4    2021  30  34  29  22  21  22  21  17  23  ...  15  15  28  20  23  19   
5    2022  33  23  27  27  31  27  14  21  26  ...  14  23  27  19  22  18   

DAY  28  29  30  31  
3    14  16  14  19  
4    20  16  27  13  
5    25  11  22  13  

[3 rows x 32 columns]

In [11]:
grouped_YEAR_MONTH = overdose_calls.groupby(['YEAR', 'MONTH']).size().reset_index(name='CALLS')
pivot_YEAR_MONTH = grouped_YEAR_MONTH.pivot_table(index='YEAR', columns='MONTH', values='CALLS', fill_value=0)
pivot_YEAR_MONTH.reset_index(inplace=True)
pivot_YEAR_MONTH

MONTH  YEAR   1   2   3   4   5   6   7   8   9  10  11  12
0      2017   0   0  12  33  22  30  34  46  28  19  26  31
1      2018  17  28  20  16  20  20  28  37  38  33  41  27
2      2019  10  24  48  56  52  37  63  26  26  30  27  25
3      2020  25  34  42  25  36  44  49  89  68  51  34  41
4      2021  44  42  50  57  67  69  56  51  51  53  48  58
5      2022  42  62  50  49  66  52  76  63  58  54  51  42

### Hypothesis tests
We will do f tests with the following hypothesis that will answer the quesitons writen above the tests.

"This test generalises t-tests to 3 or more categories.

* H0: the means of the samples are equal.

* H1: at least two means of the samples are unequal.

Assumptions: in each category (i.e. sample), the observations are i.i.d. normal with the same variance." (Schmah,2023)

**Is there any evidence that there are more calls in some days of the week?**

In [12]:
grouped_data_DOW = [pivot_YEAR_DOW[DOW] for DOW in days_order]
stats.f_oneway(*grouped_data_DOW)

F_onewayResult(statistic=0.22839969366205354, pvalue=0.9646656102856227)

We don't reject the null hypothesis

**Is there any evidence that there are more calls in between days?**

In [13]:
grouped_data_DAY = [pivot_YEAR_DAY[DAY] for DAY in range(1, 32)]
stats.f_oneway(*grouped_data_DAY)

F_onewayResult(statistic=1.520542748502412, pvalue=0.05331612716299533)

We don't reject the null hypothesis

**Is there any evidence that there are more calls in between days before the 2020 (pandemic)**

In [14]:
grouped_data_DAY_preCovid = [pivot_YEAR_DAY_preCovid[DAY] for DAY in range(1, 32)]
stats.f_oneway(*grouped_data_DAY_preCovid)

F_onewayResult(statistic=2.0722101711255725, pvalue=0.007852355012808157)

We reject the null hypothesis

**Is there any evidence that there are more calls in between days after 2020 (pandemic)?**

In [15]:
grouped_data_DAY_postCovid = [pivot_YEAR_DAY_postCovid[DAY] for DAY in range(1, 32)]
stats.f_oneway(*grouped_data_DAY_postCovid)

F_onewayResult(statistic=1.9289695811434968, pvalue=0.0147411248007655)

We reject the null hypothesis

**Is there any evidence that there are more calls in some months?**

In [16]:
grouped_data_MONTH = [pivot_YEAR_MONTH[MONTH] for MONTH in range(1, 13)]
stats.f_oneway(*grouped_data_MONTH)

F_onewayResult(statistic=1.2432103762966393, pvalue=0.27969493487267544)

We don't reject the null hypothesis

**A typo in one of the test indicated that there was a difference between the months, we decided to do a tuckey test to see where the difference was (before we noticed it was a typo. Even though the reasoning for doing this test was flawed we decided to include this seciton.**

### Tuckey for months  all years available

H0: mean of group i = mean of group j

H1: mean of group i $\neq$ mean of group j

Tuckey test will test this for all the months pairwise

In [17]:
values_list_month=[]
for MONTH in range(1, 13):
    month_data = pivot_YEAR_MONTH[MONTH].values.tolist()
    values_list_month.extend(month_data)

print(values_list_month)


[0, 17, 10, 25, 44, 42, 0, 28, 24, 34, 42, 62, 12, 20, 48, 42, 50, 50, 33, 16, 56, 25, 57, 49, 22, 20, 52, 36, 67, 66, 30, 20, 37, 44, 69, 52, 34, 28, 63, 49, 56, 76, 46, 37, 26, 89, 51, 63, 28, 38, 26, 68, 51, 58, 19, 33, 30, 51, 53, 54, 26, 41, 27, 34, 48, 51, 31, 27, 25, 41, 58, 42]


In [18]:
months_in_digits = list(range(1,13))
months_in_digits

[1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12]

TukeyHSDResults

In [19]:
# RESOURCE: https://www.statology.org/tukey-test-python/
#create DataFrame to hold data
#since we have 6 years the groups consists of every 6 values
df = pd.DataFrame({'calls': [0, 17, 10, 25, 44, 42,
                             0, 28, 24, 34, 42, 62,
                             12, 20, 48, 42, 50, 50,
                             33, 16, 56, 25, 57, 49,
                             22, 20, 52, 36, 67, 66,
                             30, 20, 37, 44, 69, 52,
                             34, 28, 63, 49, 56, 76,
                             46, 37, 26, 89, 51, 63,
                             28, 38, 26, 68, 51, 58,
                             19, 33, 30, 51, 53, 54,
                             26, 41, 27, 34, 48, 51,
                             31, 27, 25, 41, 58, 42],
                   'months': np.repeat(months_in_digits, repeats=6)}) 
# Bonferotti correction doesn't take into account
a=0.05

# perform Tukey's test
tukey = pairwise_tukeyhsd(endog=df['calls'],
                          groups=df['months'],
                          alpha=a)

#display results
print(tukey)

 Multiple Comparison of Means - Tukey HSD, FWER=0.05 
group1 group2 meandiff p-adj   lower    upper  reject
-----------------------------------------------------
     1      2   8.6667 0.9992 -25.4085 42.7418  False
     1      3     14.0 0.9597 -20.0751 48.0751  False
     1      4  16.3333  0.891 -17.7418 50.4085  False
     1      5  20.8333 0.6391 -13.2418 54.9085  False
     1      6     19.0 0.7569 -15.0751 53.0751  False
     1      7     28.0  0.209  -6.0751 62.0751  False
     1      8     29.0 0.1696  -5.0751 63.0751  False
     1      9  21.8333 0.5708 -12.2418 55.9085  False
     1     10     17.0 0.8628 -17.0751 51.0751  False
     1     11  14.8333 0.9403 -19.2418 48.9085  False
     1     12  14.3333 0.9526 -19.7418 48.4085  False
     2      3   5.3333    1.0 -28.7418 39.4085  False
     2      4   7.6667 0.9998 -26.4085 41.7418  False
     2      5  12.1667 0.9858 -21.9085 46.2418  False
     2      6  10.3333 0.9963 -23.7418 44.4085  False
     2      7  19.3333 0.736

***We did not find any statistical evidence that indicates there is a difference in between every comparison of 2 different months***

### Tuckey for days before 2020

H0: mean of group i = mean of group j

H1: mean of group i $\neq$ mean of group j

Tuckey test will test this for all the days pairwise

In [20]:
days_in_digits = list(range(1,32))


In [21]:
values_list_days_preCovid=[]
for DAY in range(1, 32):
    day_data_preCovid = pivot_YEAR_DAY_preCovid[DAY].values.tolist()
    values_list_days_preCovid.extend(day_data_preCovid)

print(values_list_days_preCovid)

[14, 25, 33, 12, 13, 21, 11, 19, 22, 6, 18, 11, 13, 8, 12, 9, 9, 14, 13, 7, 17, 6, 5, 8, 10, 14, 9, 10, 11, 12, 9, 9, 12, 3, 6, 11, 8, 6, 13, 9, 10, 11, 11, 10, 11, 10, 9, 13, 7, 9, 15, 7, 12, 14, 11, 4, 11, 9, 6, 8, 6, 13, 13, 8, 13, 12, 14, 10, 9, 5, 9, 15, 10, 9, 15, 5, 12, 11, 13, 9, 11, 6, 10, 14, 8, 8, 14, 11, 12, 18, 7, 10, 14]


In [22]:
# RESOURCE: https://www.statology.org/tukey-test-python/
#create DataFrame to hold data
#since we have 6 years the groups consists of every 6 values
df = pd.DataFrame({'calls': [14, 25, 33,
                             12, 13, 21,
                             11, 19, 22,
                             6, 18, 11,
                             13, 8, 12,
                             9, 9, 14,
                             13, 7, 17,
                             6, 5, 8,
                             10, 14, 9,
                             10, 11, 12,
                             9, 9, 12,
                             3, 6, 11,
                             8, 6, 13,
                             9, 10, 11,
                             11, 10, 11,
                             10, 9, 13,
                             7, 9, 15,
                             7, 12, 14,
                             11, 4, 11,
                             9, 6, 8,
                             6, 13, 13,
                             8, 13, 12,
                             14, 10, 9,
                             5, 9, 15,
                             10, 9, 15,
                             5, 12, 11,
                             13, 9, 11,
                             6, 10, 14,
                             8, 8, 14,
                             11, 12, 18,
                             7, 10, 14],
                   'days': np.repeat(days_in_digits, repeats=3)}) 
# We won't apply bonferroti since apparently tukey test takes it into account 
a=0.05

# perform Tukey's test
tukey = pairwise_tukeyhsd(endog=df['calls'],
                          groups=df['days'],
                          alpha=a)

#display results
print(tukey)

 Multiple Comparison of Means - Tukey HSD, FWER=0.05 
group1 group2 meandiff p-adj   lower    upper  reject
-----------------------------------------------------
     1      2  -8.6667 0.6041 -21.0976  3.7643  False
     1      3  -6.6667 0.9479 -19.0976  5.7643  False
     1      4 -12.3333 0.0545 -24.7643  0.0976  False
     1      5    -13.0 0.0298 -25.4309 -0.5691   True
     1      6 -13.3333 0.0217 -25.7643 -0.9024   True
     1      7 -11.6667 0.0957 -24.0976  0.7643  False
     1      8 -17.6667 0.0002 -30.0976 -5.2357   True
     1      9    -13.0 0.0298 -25.4309 -0.5691   True
     1     10    -13.0 0.0298 -25.4309 -0.5691   True
     1     11    -14.0 0.0112 -26.4309 -1.5691   True
     1     12 -17.3333 0.0003 -29.7643 -4.9024   True
     1     13    -15.0  0.004 -27.4309 -2.5691   True
     1     14    -14.0 0.0112 -26.4309 -1.5691   True
     1     15 -13.3333 0.0217 -25.7643 -0.9024   True
     1     16 -13.3333 0.0217 -25.7643 -0.9024   True
     1     17 -13.6667 0.015

**There is significan evidence between the first day and all others except 2,3,4,7,and 30**

### Tuckey for days after and including 2020

H0: mean of group i = mean of group j

H1: mean of group i $\neq$ mean of group j

Tuckey test will test this for all the days pairwise

In [23]:
values_list_days_postCovid=[]
for DAY in range(1, 32):
    day_data_postCovid = pivot_YEAR_DAY_postCovid[DAY].values.tolist()
    values_list_days_postCovid.extend(day_data_postCovid)

print(values_list_days_postCovid)

[26, 30, 33, 24, 34, 23, 21, 29, 27, 22, 22, 27, 14, 21, 31, 18, 22, 27, 20, 21, 14, 13, 17, 21, 21, 23, 26, 12, 26, 23, 11, 19, 21, 12, 17, 9, 21, 27, 25, 18, 15, 17, 25, 14, 23, 12, 22, 21, 17, 25, 13, 20, 16, 17, 18, 18, 25, 18, 16, 23, 22, 16, 25, 18, 15, 14, 18, 15, 23, 14, 28, 27, 15, 20, 19, 14, 23, 22, 11, 19, 18, 14, 20, 25, 16, 16, 11, 14, 27, 22, 19, 13, 13]


In [24]:
# RESOURCE: https://www.statology.org/tukey-test-python/
#create DataFrame to hold data
#since we have 6 years the groups consists of every 6 values
df = pd.DataFrame({'calls': [26, 30, 33,
                             24, 34, 23,
                             21, 29, 27,
                             22, 22, 27,
                             14, 21, 31,
                             18, 22, 27,
                             20, 21, 14,
                             13, 17, 21,
                             21, 23, 26,
                             12, 26, 23,
                             11, 19, 21,
                             12, 17, 9,
                             21, 27, 25,
                             18, 15, 17,
                             25, 14, 23,
                             12, 22, 21,
                             17, 25, 13,
                             20, 16, 17,
                             18, 18, 25,
                             18, 16, 23,
                             22, 16, 25,
                             18, 15, 14,
                             18, 15, 23,
                             14, 28, 27,
                             15, 20, 19,
                             14, 23, 22,
                             11, 19, 18,
                             14, 20, 25,
                             16, 16, 11,
                             14, 27, 22,
                             19, 13, 13],
                   'days': np.repeat(days_in_digits, repeats=3)}) 
# We won't apply bonferroti since apparently tukey test takes it into account 
a=0.05

# perform Tukey's test
tukey = pairwise_tukeyhsd(endog=df['calls'],
                          groups=df['days'],
                          alpha=a)

#display results
print(tukey)

 Multiple Comparison of Means - Tukey HSD, FWER=0.05 
group1 group2 meandiff p-adj   lower    upper  reject
-----------------------------------------------------
     1      2  -2.6667    1.0 -17.9591 12.6258  False
     1      3     -4.0    1.0 -19.2925 11.2925  False
     1      4     -6.0 0.9993 -21.2925  9.2925  False
     1      5  -7.6667 0.9755 -22.9591  7.6258  False
     1      6  -7.3333 0.9858 -22.6258  7.9591  False
     1      7 -11.3333 0.4774 -26.6258  3.9591  False
     1      8 -12.6667 0.2599 -27.9591  2.6258  False
     1      9  -6.3333 0.9983 -21.6258  8.9591  False
     1     10  -9.3333  0.831 -24.6258  5.9591  False
     1     11 -12.6667 0.2599 -27.9591  2.6258  False
     1     12    -17.0 0.0135 -32.2925 -1.7075   True
     1     13  -5.3333 0.9999 -20.6258  9.9591  False
     1     14    -13.0 0.2174 -28.2925  2.2925  False
     1     15     -9.0 0.8742 -24.2925  6.2925  False
     1     16 -11.3333 0.4774 -26.6258  3.9591  False
     1     17 -11.3333 0.477

**There is a difference between the first day and the 12th the first day and the 29th**

## Visualizations

In [25]:
overdose_month_narcan = alt.Chart(overdose_calls).encode(
    x=alt.X('MONTH:O', title='Months of the year'),
    y=alt.Y('count()', title='Number of calls'),
    color=alt.Color('NARCAN_ADM:N',title='Narcan Administered')
).mark_bar().properties()

overdose_month_narcan_year = alt.Chart(overdose_calls).encode(
    column=alt.Column('YEAR'),
    x=alt.X('MONTH:O', title='Months of the year'),
    y=alt.Y('count()', title='Number of calls'),
    color=alt.Color('NARCAN_ADM:N',title='Narcan Administered')
).mark_bar().properties()

overdose_month_narcan | overdose_month_narcan_year

alt.HConcatChart(...)

In [26]:
overdose_week_narcan = alt.Chart(overdose_calls).encode(
    column=alt.Column('YEAR'),
    x=alt.X('DOW', title='Day of the week',sort=days_order),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar().properties().interactive()

overdose_week_narcan 

alt.Chart(...)

In [27]:
overdose_week_narcan_full = alt.Chart(overdose_calls).encode(
    x=alt.X('DOW', title='Day of the week',sort=days_order),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar().properties().interactive()

overdose_week_narcan_full

alt.Chart(...)

In [28]:
overdose_calls[overdose_calls['YEAR']==2017]['MONTH'].unique()

array([ 8,  7,  6,  4,  3,  5, 11, 12, 10,  9], dtype=int64)

In [29]:
overdose_days_narcan2017 = alt.Chart(overdose_calls[overdose_calls['YEAR']==2017]).encode(
    x=alt.X('DAY', title='Day number'),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar(size=5).properties(
    title='2017'
).facet(
    column='MONTH:O'
)

overdose_days_narcan2018 = alt.Chart(overdose_calls[overdose_calls['YEAR']==2018]).encode(
    x=alt.X('DAY', title='Day number'),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar(size=5).properties(
    title='2018'
).facet(
    column='MONTH:O'
)

overdose_days_narcan2019 = alt.Chart(overdose_calls[overdose_calls['YEAR']==2019]).encode(
    x=alt.X('DAY', title='Day number'),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar(size=5).properties(
    title='2019'
).facet(
    column='MONTH:O'
)

overdose_days_narcan2020 = alt.Chart(overdose_calls[overdose_calls['YEAR']==2020]).encode(
    x=alt.X('DAY', title='Day number'),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar(size=5).properties(
    title='2020'
).facet(
    column='MONTH:O'
)

overdose_days_narcan2021 = alt.Chart(overdose_calls[overdose_calls['YEAR']==2021]).encode(
    x=alt.X('DAY', title='Day number'),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar(size=5).properties(
    title='2021'
).facet(
    column='MONTH:O'
)

overdose_days_narcan2022 = alt.Chart(overdose_calls[overdose_calls['YEAR']==2022]).encode(
    x=alt.X('DAY', title='Day number'),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar(size=5).properties(
    title='2022'
).facet(
    column='MONTH:O'
)

overdose_days_narcan2017 & overdose_days_narcan2018 & overdose_days_narcan2019 &overdose_days_narcan2020 &overdose_days_narcan2021 &overdose_days_narcan2022

alt.VConcatChart(...)

In [30]:
overdose_week_narcan = alt.Chart(overdose_calls).encode(
    x=alt.X('DAY', title='Day number'),
    y=alt.Y('count()', title='Number of calls'),
).mark_bar().properties().facet(
    column='MONTH:O'
)

overdose_week_narcan 

alt.FacetChart(...)

In [31]:
overdose_day_preCovid = alt.Chart(overdose_calls_preCovid).encode(
    x=alt.X('DAY:O', title='Day number'),
    y=alt.Y('count():Q', title='Number of calls'),
).mark_bar().properties()

overdose_day_preCovid

alt.Chart(...)

In [32]:
overdose_day_narcan = alt.Chart(overdose_calls).encode(
    x=alt.X('DAY:O', title='Day number'),
    y=alt.Y('count():Q', title='Number of calls'),
).mark_bar().properties()

overdose_day_narcan 

alt.Chart(...)

In [33]:
overdose_day_postCovid = alt.Chart(overdose_calls_postCovid).encode(
    x=alt.X('DAY:O', title='Day number'),
    y=alt.Y('count():Q', title='Number of calls'),
).mark_bar().properties()

overdose_day_postCovid

alt.Chart(...)

In [34]:
overdose_day_postCovid = alt.Chart(overdose_calls_postCovid).encode(
    x=alt.X('DAY:O', title='Day number').bin(),
    y=alt.Y('count():Q', title='Number of calls'),
).mark_bar().properties()

overdose_day_postCovid

alt.Chart(...)

In [35]:
overdose_year_narcan = alt.Chart(overdose_calls).encode(
    column=alt.Column('YEAR'),
    x=alt.X('NARCAN_ADM', title='Year'),
    y=alt.Y('count():Q', title='Number of calls'),
    color=alt.Color('NARCAN_ADM:N',title='Narcan Administered')
).mark_bar().properties().interactive()


overdose_year = alt.Chart(overdose_calls).encode(
    x=alt.X('YEAR:O', title='Year'),
    y=alt.Y('count():Q', title='Number of calls').scale(domain=(0, 1100)),
    color=alt.Color('NARCAN_ADM:N',title='Narcan Administered')
).mark_bar().properties().interactive()

overdose_year_narcan | overdose_year

alt.HConcatChart(...)

In [36]:
overdose_year

alt.Chart(...)

In [37]:
overdose_year_plot = alt.Chart(overdose_calls).encode(
    x=alt.X('YEAR:O', title='Year'),
    y=alt.Y('count():Q', title='Number of calls')
).mark_bar().properties().interactive()
overdose_year_plot

alt.Chart(...)

## Overdose related visits to the hospital by month

In [38]:
overdose_emergency_month = pd.read_csv('../clean_datasets/overdose_emergency_visits_by_month.csv')

In [39]:
overdose_emergency_month.head()

Month  Total ED visits for opioid overdose  Year
0   Apr                                   38  2017
1   May                                   24  2017
2   Jun                                   37  2017
3   Jul                                   50  2017
4   Aug                                   48  2017

In [40]:
months_order = ["Jan", "Feb", "Mar", "Apr", "May", "Jun", "Jul","Aug","Sep","Oct","Nov","Dec"]


## Visualizations

In [41]:
overdose_month= alt.Chart(overdose_emergency_month).encode(
    column=alt.Column('Year'),
    x=alt.X('Month:O', title='Month',sort=months_order),
    y=alt.Y('Total ED visits for opioid overdose:Q', title='Number of individuals'),
    color=alt.Color('Month',title='Month')
).mark_bar().properties()



overdose_month

alt.Chart(...)

In [42]:
overdose_month_by_year= alt.Chart(overdose_emergency_month).encode(
    x=alt.X('Year:O', title='Year'),
    y=alt.Y('Total ED visits for opioid overdose:Q', title='Number of individuals'),
).mark_bar().properties()



overdose_month_by_year

alt.Chart(...)

## Hypothesis Test

"This test generalises t-tests to 3 or more categories.

* H0: the means of the samples are equal.

* H1: at least two means of the samples are unequal.

Assumptions: in each category (i.e. sample), the observations are i.i.d. normal with the same variance." (Schmah,2023)

**Are there any substantial differences in between the number of people that went to the hospitals for overdoses in each month**

In [43]:
grouped_data_months = [overdose_emergency_month['Total ED visits for opioid overdose'][overdose_emergency_month['Month'] == month] for month in overdose_emergency_month['Month'].unique()]
stats.f_oneway(*grouped_data_months)

F_onewayResult(statistic=0.6199876756552681, pvalue=0.8052410368308273)

**Are there any substantial differences in between the number of people that went to the hospitals for overdoses before and after covid. Is the amount greater after covid?**

Hypothesis

 H0: PreCovid= PostCovid
   
 H1: PreCovid < PostCovid

In [44]:
overdose_emergency_month_preCovid=overdose_emergency_month['Total ED visits for opioid overdose'][overdose_emergency_month['Year']<2020]

In [45]:
overdose_emergency_month_postCovid=overdose_emergency_month['Total ED visits for opioid overdose'][overdose_emergency_month['Year']>=2020]


In [46]:
stats.ttest_ind(overdose_emergency_month_preCovid, overdose_emergency_month_postCovid,alternative='less', equal_var=False)

TtestResult(statistic=-10.515055305697738, pvalue=1.0450309978392072e-15, df=61.94464937758678)

We reject the null hypothesis

## Overdose related deaths

In [47]:
opioid_related_deaths=pd.read_csv('../clean_datasets/overdose_related_deaths.csv')
opioid_related_deaths.head()

Quarter  Confirmed_opioid_related_deaths  Year
0      Q2                               13  2017
1      Q3                               28  2017
2      Q4                               13  2017
3      Q1                               14  2018
4      Q2                               14  2018

## Hypothesis Test

"This test generalises t-tests to 3 or more categories.

* H0: the means of the samples are equal.

* H1: at least two means of the samples are unequal.

Assumptions: in each category (i.e. sample), the observations are i.i.d. normal with the same variance." (Schmah,2023)

**Is there a statistically significant difference between the quarters**

In [48]:
grouped_data_opioid_deaths = [opioid_related_deaths['Confirmed_opioid_related_deaths'][opioid_related_deaths['Quarter'] == quarter] for quarter in opioid_related_deaths['Quarter'].unique()]
stats.f_oneway(*grouped_data_opioid_deaths)

F_onewayResult(statistic=0.07585972265023112, pvalue=0.9723276431538354)

**Are there any substantial differences in between the number of people that died from overdoses . Is the amount greater after covid(not including 2023 since we don't have enough data)?**

Hypothesis

 H0: PreCovid= PostCovid
   
 H1: PreCovid < PostCovid

In [49]:
opioid_related_deaths_preCovid=opioid_related_deaths['Confirmed_opioid_related_deaths'][opioid_related_deaths['Year']<2020]

In [50]:
opioid_related_deaths_postCovid=opioid_related_deaths[(opioid_related_deaths['Year']>=2020) &  (opioid_related_deaths['Year']<2023)]

In [51]:
opioid_related_deaths_postCovid=opioid_related_deaths_postCovid['Confirmed_opioid_related_deaths']

In [52]:
stats.ttest_ind(opioid_related_deaths_preCovid, opioid_related_deaths_postCovid,alternative='less', equal_var=False)

TtestResult(statistic=-5.479026997752909, pvalue=1.1047059364398779e-05, df=20.256784199034975)

## Visualizations

In [53]:
quarters_order = ["Q1", "Q2", "Q3", "Q4"]

In [54]:
overdose_quarter= alt.Chart(opioid_related_deaths).encode(
    column=alt.Column('Year'),
    x=alt.X('Quarter:O', title='Quarter',sort=quarters_order),
    y=alt.Y('Confirmed_opioid_related_deaths:Q', title='Confirmed opioid related deaths'),
    color=alt.Color('Quarter',title='Quarter')
).mark_bar().properties()



overdose_quarter

alt.Chart(...)

In [55]:
overdose_quarter_complete= alt.Chart(opioid_related_deaths).encode(
    x=alt.X('Quarter:O', title='Quarter',sort=quarters_order),
    y=alt.Y('Confirmed_opioid_related_deaths:Q', title='Confirmed opioid related deaths'),
    color=alt.Color('Quarter',title='Quarter')
).mark_bar().properties()



overdose_quarter_complete

alt.Chart(...)

In [56]:
column_sum = opioid_related_deaths['Confirmed_opioid_related_deaths'].sum()

print("Confirmed opioid related deaths from March 2017 to June 2023:", column_sum)

Confirmed opioid related deaths from March 2017 to June 2023: 726


In [57]:
first_six_months_2023 =opioid_related_deaths[opioid_related_deaths['Year']==2023]['Confirmed_opioid_related_deaths'].sum()
print("Confirmed opioid related deaths first 6 months of 2023:", first_six_months_2023)

Confirmed opioid related deaths first 6 months of 2023: 93


In [58]:
overdose_quarter= alt.Chart(opioid_related_deaths).encode(
    x=alt.X('Year:O', title='Year'),
    y=alt.Y('Confirmed_opioid_related_deaths:Q', title='Confirmed opioid related deaths').scale(domain=(0, 1100)),
    color=alt.Color('Quarter:O',title='Quarter')
).mark_bar().properties()


#first is calls second is deaths for 2023 it is only the first 6 months and it is already bigger than the las
overdose_year | overdose_quarter |  overdose_month_by_year

alt.HConcatChart(...)

In [59]:
overdose_quarter_nonScaled= alt.Chart(opioid_related_deaths).encode(
    x=alt.X('Year:O', title='Year'),
    y=alt.Y('Confirmed_opioid_related_deaths:Q', title='Confirmed opioid related deaths'),
    color=alt.Color('Quarter:O',title='Quarter')
).mark_bar().properties()

overdose_quarter_nonScaled

alt.Chart(...)